#### BSV step 2 for sub-volume cluter, and EDI table generation

In [1]:
import numpy as np
import pandas as pd
import glob
import os

from sklearn.preprocessing import StandardScaler
from sklearn.mixture import GaussianMixture

# from matplotlib.patches import Ellipse

In [2]:
'''
return the K value and covariance_type from the best GMM model according to the BIC
'''
def get_K(feature, K_num):
    lowest_bic = np.infty
    bic = []
    n_components_range = range(1, K_num+1)
    # cv_types = ["spherical", "tied", "diag", "full"]
    cv_types = ["full"]
    for cv_type in cv_types:
        for n_components in n_components_range:
            # Fit a Gaussian mixture with EM
            gmm = GaussianMixture(
                n_components=n_components, covariance_type=cv_type,random_state=0
            )
            gmm.fit(feature)
            bic.append(gmm.bic(feature))
            if bic[-1] < lowest_bic:
                lowest_bic = bic[-1]
                best_gmm = gmm

    bic = np.array(bic)
    
    return best_gmm.n_components, best_gmm.covariance_type

'''
For each feature, assign a K value based on GMM(BIC)
Assume each patient has N features, return a list with shape (1,N) which include K for each feature
'''
def assign_K_value2features(Patient_features, K_num):
    x, y = Patient_features.shape
    K_list = []
    cov_type_list = []
    for feature_idx in range(0, y):
        X_train = np.array(Patient_features.iloc[:, feature_idx]).reshape(-1,1)
        k, cov_type = get_K(X_train, K_num)
        K_list.append(k)
        cov_type_list.append(cov_type)

    return K_list, cov_type_list


In [3]:
def RFtable_generate(path,mode):
    df = pd.read_csv(path)
    df.dropna(inplace=True)
    c_name_list = df.columns.to_list()

    # Since some features are not used, we only select first order and texture features for now
    c_rest_list = ['firstorder','glcm','glrlm','glszm','gldm','ngtdm']
    rest_cname_list = []
    for feature_type in c_rest_list:
        for c_names in c_name_list:
            if feature_type in c_names:
                rest_cname_list.append(c_names)

    df_rest_origin = df.loc[:,rest_cname_list]
    if mode == 'Z-socre':
        #TODO column name 有点问题
        df_rest = pd.DataFrame(data = StandardScaler().fit_transform(df_rest_origin),columns=df_rest_origin.columns)
    else:
        df_rest = df_rest_origin
    return df_rest

In [4]:
# User parameters

# feature_dir = '/home/zhenwei/Documents/ProjectCode/image_processing/SVoxel/output_SY/RF'
# EDI_dir = '/home/zhenwei/Documents/ProjectCode/image_processing/SVoxel/output_SY/EDI'

feature_dir = r'D:\03_AIDataSet\00_Radiomics\Dataset\QMITH\output\RF'
EDI_dir = r'D:\03_AIDataSet\00_Radiomics\Dataset\QMITH\output\EDI'

if not os.path.exists(EDI_dir):
    os.makedirs(EDI_dir)

center = 'HN'
K_num = 5   # EDI range 1-5, can be set 10 as well

Patients_K = pd.DataFrame()
Patients_covtype = []

files = glob.glob(os.path.join(feature_dir,'*.csv'))
ptid_list = []
ptid_nan = []
ptid_K0 = []

for i in range(len(files)):
    ptid = files[i].split('_')[-2].split('\\')[-1]
    df_feature =pd.read_csv(files[i])
    df_feature.dropna(inplace=True)
    if df_feature.isnull().values.any():
        ptid_nan.append(files[i]) # record table has NaN
    else:
        ptid = files[i].split('_')[-2].split('\\')[-1]
        ptid_list.append(ptid)
        print('processing: ',ptid)

        # TODO not sure if normalization is useful for discrete numbers
        # df_rest = RFtable_generate(files[i],'Z-socre')
        df_rest = RFtable_generate(files[i],'')

        K, cov_type_list = assign_K_value2features(df_rest, K_num)
        try:
            if sum(K) !=0:
                K_new = [ptid] + K
                tmp_df_K = pd.DataFrame(data = K_new).T
                tmp_df_K.columns = ['ID']+ df_rest.columns.to_list()
                Patients_K = pd.concat([Patients_K,tmp_df_K])
            else:
                ptid_K0.append(ptid)
                print('something wrong: K is 0')
        except:
            print('Error: someting wrong about K')
            # cov types are important, but not investigated for now
        Patients_covtype.append(cov_type_list)
        print('Patient-',files[i].split('_')[-2].split('\\')[-1], ' done!')

# save table in a specified directory
Patients_K.to_csv(os.path.join(EDI_dir,center+'_BSV_EDI_k5.csv'),index = False)

processing:  001


c:\Users\sunpe\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\sunpe\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\sunpe\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\sunpe\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Window

Patient- 001  done!
processing:  002


c:\Users\sunpe\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\sunpe\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\sunpe\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\sunpe\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Window

Patient- 002  done!
processing:  003


c:\Users\sunpe\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\sunpe\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\sunpe\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\sunpe\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Window

Patient- 003  done!
processing:  004


c:\Users\sunpe\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\sunpe\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\sunpe\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\sunpe\anaconda3\Lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Window

Patient- 004  done!


#### Generate full ED table with clinical outcome

In [ ]:
c_path = '/home/zhenwei/Documents/ProjectCode/image_processing/data/'
EDI_path = '/home/zhenwei/Documents/ProjectCode/image_processing/SVoxel/output_HN/EDI'

df_c = pd.read_csv(os.path.join(c_path,center + '_ClinicalData.csv'))
df_BSV = pd.read_csv(os.path.join(EDI_path, center + '_BSV_EDI_k10.csv'))

df_merge = df_c.merge(df_BSV,on='ID')
df_merge.to_csv(os.path.join(EDI_path,center + '_BSV_EDI__k10_full.csv'),index=False)